In [4]:
import os
import torch
from torch import nn
from torch.utils.data import DataLoader, Dataset
from transformers import BertTokenizer, BertModel, AdamW, get_linear_schedule_with_warmup
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
import pandas as pd

ModuleNotFoundError: No module named 'torch'

In [ ]:
import os
current_directory = os.getcwd()
print(current_directory)


/content


In [ ]:
pip install transformers


Defaulting to user installation because normal site-packages is not writeable
     ---------------------------------------- 0.0/123.5 kB ? eta -:--:--
     --- ------------------------------------ 10.2/123.5 kB ? eta -:--:--
     --- ------------------------------------ 10.2/123.5 kB ? eta -:--:--
     --- ------------------------------------ 10.2/123.5 kB ? eta -:--:--
     --- ------------------------------------ 10.2/123.5 kB ? eta -:--:--
     ------------ ------------------------ 41.0/123.5 kB 164.3 kB/s eta 0:00:01
     ------------------ ------------------ 61.4/123.5 kB 204.8 kB/s eta 0:00:01
     ------------------ ------------------ 61.4/123.5 kB 204.8 kB/s eta 0:00:01
     ------------------ ------------------ 61.4/123.5 kB 204.8 kB/s eta 0:00:01
     -------------------------------- --- 112.6/123.5 kB 252.2 kB/s eta 0:00:01
     ------------------------------------ 123.5/123.5 kB 278.9 kB/s eta 0:00:00
     ---------------------------------------- 0.0/318.5 kB ? eta -:--:--


  error: subprocess-exited-with-error
  
  × Preparing metadata (pyproject.toml) did not run successfully.
  │ exit code: 1
  ╰─> [6 lines of output]
      Checking for Rust toolchain....
      
      Cargo, the Rust package manager, is not installed or is not on PATH.
      This package requires Rust and Cargo to compile extensions. Install it through
      the system's package manager or via https://rustup.rs/
      
      [end of output]
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
error: metadata-generation-failed

× Encountered error while generating package metadata.
╰─> See above for output.

note: This is an issue with the package mentioned above, not pip.
hint: See above for details.


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df=pd.read_csv("/Twitter_Data.csv")

In [ ]:
df

clean_text  category
0       when modi promised “minimum government maximum...      -1.0
1       talk all the nonsense and continue all the dra...       0.0
2       what did just say vote for modi  welcome bjp t...       1.0
3       asking his supporters prefix chowkidar their n...       1.0
4       answer who among these the most powerful world...       1.0
...                                                   ...       ...
139418  per capita income average indians have gone wh...       1.0
139419  wow what response behold all south bangalorean...       1.0
139420                       modi also not visited there        0.0
139421  does his categorisation cover bjp many states ...       1.0
139422  problembut take responsibility for unprecedent...       NaN

[139423 rows x 2 columns]

In [ ]:
df = df[df['category'] != 0.0]

In [ ]:
df

clean_text  category
0      when modi promised “minimum government maximum...      -1.0
2      what did just say vote for modi  welcome bjp t...       1.0
3      asking his supporters prefix chowkidar their n...       1.0
4      answer who among these the most powerful world...       1.0
8      with upcoming election india saga going import...       1.0
...                                                  ...       ...
16084  this scheme very good but the congress governm...       1.0
16085  sorry modi came 2001 kindly see the condition ...       1.0
16086  feels like total conspiracy holding the seat t...       1.0
16088  told them love and respect their president the...       1.0
16089                 imagine the hatred modi and shah h       NaN

[10518 rows x 2 columns]

In [ ]:
import pandas as pd

def load_imdb_data(df):
    df = df.sample(3000)
    texts = df['clean_text'].tolist()

    labels = []
    for sentiment in df['category'].tolist():
        if sentiment == 1.0:
            labels.append(1)

        else:  # Assuming all other sentiments are "negative"
            labels.append(0)

    return texts, labels


In [ ]:
#data_file = "/Twitter_Data.csv"
texts, labels = load_imdb_data(df)


In [ ]:
#TextClassificationDataset
class TextClassificationDataset(Dataset):
    def __init__(self, texts, labels, tokenizer, max_length):
        self.texts = texts
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        text = self.texts[idx]
        label = self.labels[idx]
        encoding = self.tokenizer(text, return_tensors='pt', max_length=self.max_length, padding='max_length', truncation=True)
        return {'input_ids': encoding['input_ids'].flatten(), 'attention_mask': encoding['attention_mask'].flatten(), 'label': torch.tensor(label)}


In [ ]:
class BERTClassifier(nn.Module):
    def __init__(self, bert_model_name, num_classes):
        super(BERTClassifier, self).__init__()
        self.bert = BertModel.from_pretrained(bert_model_name)
        self.dropout = nn.Dropout(0.1)
        self.fc = nn.Linear(self.bert.config.hidden_size, num_classes)

def forward(self, input_ids, attention_mask):
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        pooled_output = outputs.pooler_output
        x = self.dropout(pooled_output)
        logits = self.fc(x)
        return logits

In [ ]:
# Training loop
def train(model, data_loader, optimizer, scheduler, device):
    model.train()
    for batch in data_loader:
        optimizer.zero_grad()
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['label'].to(device)
        outputs = model(input_ids=input_ids, attention_mask=attention_mask, labels=labels)  # Corrected this line
        loss = outputs.loss
        loss.backward()
        optimizer.step()
        scheduler.step()


In [ ]:
def evaluate(model, data_loader, device):
    model.eval()
    predictions = []
    actual_labels = []

    with torch.no_grad():
        for batch in data_loader:
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['label'].to(device)

            outputs = model(input_ids=input_ids, attention_mask=attention_mask)
            logits = outputs.logits  # Access the logits

            _, preds = torch.max(logits, dim=1)  # Apply argmax to logits
            predictions.extend(preds.cpu().tolist())
            actual_labels.extend(labels.cpu().tolist())

    accuracy = accuracy_score(actual_labels, predictions)
    report = classification_report(actual_labels, predictions, target_names=['class_0', 'class_1'])  # Adjust target_names as needed

    return accuracy, report


In [ ]:
import torch

def predict_sentiment(text, model, tokenizer, device, max_length=128):
    # Tokenize input text
    inputs = tokenizer(text, max_length=max_length, padding=True, truncation=True, return_tensors="pt")
    input_ids = inputs["input_ids"].to(device)
    attention_mask = inputs["attention_mask"].to(device)

    # Make prediction
    with torch.no_grad():
        outputs = model(input_ids=input_ids, attention_mask=attention_mask)
        logits = outputs.logits
        predicted_class = torch.argmax(logits, dim=1).item()

    if predicted_class == 1:
        return "positive"
    else:
      return "negative"


In [ ]:
# Set up parameters
bert_model_name = 'bert-base-uncased'
num_classes = 2
max_length = 128
batch_size = 16
num_epochs = 1
learning_rate = 2e-5


In [ ]:
train_texts, val_texts, train_labels, val_labels = train_test_split(texts, labels, test_size=0.2, random_state=42)

In [ ]:
tokenizer = BertTokenizer.from_pretrained(bert_model_name)
train_dataset = TextClassificationDataset(train_texts, train_labels, tokenizer, max_length)
val_dataset = TextClassificationDataset(val_texts, val_labels, tokenizer, max_length)
train_dataloader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_dataloader = DataLoader(val_dataset, batch_size=batch_size)

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = BERTClassifier(bert_model_name, num_classes).to(device)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
optimizer = AdamW(model.parameters(), lr=learning_rate)
total_steps = len(train_dataloader) * num_epochs
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=0, num_training_steps=total_steps)

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [ ]:
pip install accelerate>=0.20.1


In [ ]:
from transformers import TrainingArguments, Trainer


In [ ]:

pip install transformers[torch,accelerate]>=0.20.1


In [ ]:
def forward(self, input_ids, attention_mask):
    outputs = self.bert(input_ids, attention_mask=attention_mask)
    pooled_output = outputs.pooler_output
    x = self.dropout(pooled_output)
    logits = self.fc(x)
    return logits


In [ ]:
from transformers import BertForSequenceClassification

class BERTClassifier(nn.Module):
    def __init__(self, bert_model_name, num_classes):
        super(BERTClassifier, self).__init__()
        self.bert = BertForSequenceClassification.from_pretrained(bert_model_name, num_labels=num_classes)

    def forward(self, input_ids, attention_mask):
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        logits = outputs.logits
        return logits


In [ ]:
pip install transformers>=4.11.0,<5.0.0 torch>=1.8.0,<1.9.0


/bin/bash: line 1: 5.0.0: No such file or directory


In [ ]:
pip install transformers

In [ ]:
import torch
import pandas as pd
from transformers import BertTokenizer, BertForSequenceClassification, AdamW, get_linear_schedule_with_warmup
from torch.utils.data import DataLoader, Dataset
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report

# Define your dataset loading function and TextClassificationDataset class

# Define your BERT model and training functions

# Set up parameters
bert_model_name = 'bert-base-uncased'
num_classes = 2
max_length = 128
batch_size = 16
num_epochs = 2
learning_rate = 2e-5

# Load and preprocess your data

# Initialize BERT tokenizer
tokenizer = BertTokenizer.from_pretrained(bert_model_name)

# Create datasets and dataloaders

# Set up device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Initialize BERT model
model = BertForSequenceClassification.from_pretrained(bert_model_name, num_labels=num_classes)
model.to(device)

# Initialize optimizer and scheduler
optimizer = AdamW(model.parameters(), lr=learning_rate)
total_steps = len(train_dataloader) * num_epochs
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=0, num_training_steps=total_steps)

# Training and evaluation loop
for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1}/{num_epochs}")

    # Training phase
    train(model, train_dataloader, optimizer, scheduler, device)

    # Evaluation phase
    accuracy, report = evaluate(model, val_dataloader, device)
    print(f"Validation Accuracy: {accuracy:.4f}")
    print(report)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Epoch 1/2
Validation Accuracy: 0.7583
              precision    recall  f1-score   support

     class_0       0.64      0.64      0.64       202
     class_1       0.82      0.82      0.82       398

    accuracy                           0.76       600
   macro avg       0.73      0.73      0.73       600
weighted avg       0.76      0.76      0.76       600

Epoch 2/2
Validation Accuracy: 0.7917
              precision    recall  f1-score   support

     class_0       0.71      0.64      0.68       202
     class_1       0.83      0.87      0.85       398

    accuracy                           0.79       600
   macro avg       0.77      0.76      0.76       600
weighted avg       0.79      0.79      0.79       600



In [ ]:
#saving model

torch.save(model.state_dict(), "bert_classifier.pth")

NameError: name 'torch' is not defined

In [ ]:
# Test sentiment prediction
test_text = "modi is a prime minister,but made many worst changes"
sentiment = predict_sentiment(test_text, model, tokenizer, device)


print(f"Predicted sentiment: {sentiment}")

Predicted sentiment: negative


**TWITTER** **DATASET**

In [ ]:
df=pd.read_csv("/content/drive/MyDrive/Colab Notebooks/Twitter_Data.csv")

In [ ]:
df

clean_text  category
0       when modi promised “minimum government maximum...      -1.0
1       talk all the nonsense and continue all the dra...       0.0
2       what did just say vote for modi  welcome bjp t...       1.0
3       asking his supporters prefix chowkidar their n...       1.0
4       answer who among these the most powerful world...       1.0
...                                                   ...       ...
162975  why these 456 crores paid neerav modi not reco...      -1.0
162976  dear rss terrorist payal gawar what about modi...      -1.0
162977  did you cover her interaction forum where she ...       0.0
162978  there big project came into india modi dream p...       0.0
162979  have you ever listen about like gurukul where ...       1.0

[162980 rows x 2 columns]

In [ ]:
import pandas as pd

def load_twitter_data(data_file):
    df = pd.read_csv(data_file)
    df = df.sample(3000)  # Sample 3000 rows if needed

    texts = df['clean_text'].tolist()

    labels = []
    for category in df['category'].tolist():
        # Assuming that the categories in the Twitter dataset are "positive," "neutral," and "negative"
        if category == "positive":
            labels.append(1)
        elif category == "neutral":
            labels.append(0)
        else:
            labels.append(2)  # Assuming all other categories are "negative"

    return texts, labels


In [ ]:
data_file = "/content/drive/MyDrive/Colab Notebooks/Twitter_Data.csv"
texts, labels = load_twitter_data(data_file)

NameError: ignored

In [ ]:
from torch.utils.data import Dataset
import torch

class TwitterClassificationDataset(Dataset):
    def __init__(self, texts, labels, tokenizer, max_length):
        self.texts = texts
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        text = self.texts[idx]
        label = self.labels[idx]
        encoding = self.tokenizer(text, return_tensors='pt', max_length=self.max_length, padding='max_length', truncation=True)
        return {'input_ids': encoding['input_ids'].flatten(), 'attention_mask': encoding['attention_mask'].flatten(), 'label': torch.tensor(label)}


In [ ]:
pip install transformers

In [ ]:
import torch
import torch.nn as nn
from transformers import BertModel

class BERTClassifier(nn.Module):
    def __init__(self, bert_model_name, num_classes):
        super(BERTClassifier, self).__init__()
        self.bert = BertModel.from_pretrained(bert_model_name)
        self.dropout = nn.Dropout(0.1)
        self.fc = nn.Linear(self.bert.config.hidden_size, num_classes)

    def forward(self, input_ids, attention_mask):
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        pooled_output = outputs.pooler_output
        x = self.dropout(pooled_output)
        logits = self.fc(x)
        return logits


In [ ]:
def train(model, data_loader, optimizer, scheduler, device):
    model.train()
    for batch in data_loader:
        optimizer.zero_grad()
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['label'].to(device)
        outputs = model(input_ids=input_ids, attention_mask=attention_mask, labels=labels)
        loss = outputs.loss
        loss.backward()
        optimizer.step()
        scheduler.step()


In [ ]:
def evaluate(model, data_loader, device):
    model.eval()
    predictions = []
    actual_labels = []

    with torch.no_grad():
        for batch in data_loader:
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['label'].to(device)

            outputs = model(input_ids=input_ids, attention_mask=attention_mask)
            logits = outputs.logits  # Access the logits

            _, preds = torch.max(logits, dim=1)  # Apply argmax to logits
            predictions.extend(preds.cpu().tolist())
            actual_labels.extend(labels.cpu().tolist())

    # Modify target_names to match your class labels
    target_names = ['positive', 'neutral', 'negative']

    accuracy = accuracy_score(actual_labels, predictions)
    report = classification_report(actual_labels, predictions, target_names=target_names)

    return accuracy, report


In [ ]:
import torch

def predict_sentiment(text, model, tokenizer, device, max_length=128):
    # Tokenize and prepare the input
    inputs = tokenizer(
        text,
        truncation=True,
        padding=True,
        max_length=max_length,
        return_tensors="pt"
    )
    input_ids = inputs["input_ids"].to(device)
    attention_mask = inputs["attention_mask"].to(device)

    # Get model predictions
    with torch.no_grad():
        outputs = model(input_ids=input_ids, attention_mask=attention_mask)
        logits = outputs.logits
        _, preds = torch.max(logits, dim=1)

    if preds.item() == 1:
        return "positive"
    elif preds.item() == 0:
        return "neutral"
    else:
        return "negative"

In [ ]:
# Set up parameters
bert_model_name = 'bert-base-uncased'
num_classes = 2
max_length = 128
batch_size = 4
num_epochs = 1
learning_rate = 2e-5

In [ ]:
  from sklearn.model_selection import train_test_split
  train_texts, val_texts, train_labels, val_labels = train_test_split(texts, labels, test_size=0.2, random_state=42)



In [ ]:
from transformers import BertTokenizer

# Define your BERT model and tokenizer
bert_model_name = 'bert-base-uncased'
tokenizer = BertTokenizer.from_pretrained(bert_model_name)

# Create your datasets and dataloaders
train_dataset = TwitterClassificationDataset(train_texts, train_labels, tokenizer, max_length)
val_dataset = TwitterClassificationDataset(val_texts, val_labels, tokenizer, max_length)

train_dataloader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_dataloader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)


In [ ]:
# Define your optimizer and scheduler
optimizer = AdamW(model.parameters(), lr=learning_rate)
total_steps = len(train_dataloader) * num_epochs
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=0, num_training_steps=total_steps)


/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [ ]:
pip install accelerate>=0.20.1

In [ ]:
from transformers import TrainingArguments, Trainer

In [ ]:
pip install transformers[torch,accelerate]>=0.20.1

In [ ]:
def forward(self, input_ids, attention_mask):
    outputs = self.bert(input_ids, attention_mask=attention_mask)
    pooled_output = outputs.pooler_output
    x = self.dropout(pooled_output)
    logits = self.fc(x)
    return logits

In [ ]:
from transformers import BertForSequenceClassification

class BERTTwitterClassifier(nn.Module):
    def __init__(self, bert_model_name, num_classes):
        super(BERTTwitterClassifier, self).__init__()
        self.bert = BertForSequenceClassification.from_pretrained(bert_model_name, num_labels=num_classes)

    def forward(self, input_ids, attention_mask):
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        logits = outputs.logits
        return logits


In [ ]:
pip install transformers>=4.11.0,<5.0.0 torch>=1.8.0,<1.9.0

/bin/bash: line 1: 5.0.0: No such file or directory


In [ ]:
pip install transformers

In [ ]:
import torch
import torch.nn as nn
from transformers import BertTokenizer, AdamW, get_linear_schedule_with_warmup
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import train_test_split
import pandas as pd

# Load the Twitter dataset
data_file = "/content/drive/MyDrive/Colab Notebooks/Twitter_Data.csv"
df = pd.read_csv(data_file)

# Define a function to load and preprocess the Twitter data
def load_twitter_data(data_file, num_samples=None):
    df = pd.read_csv(data_file)
    if num_samples is not None:
        df = df.sample(num_samples)  # Sample a subset of the data if needed

    texts = df['clean_text'].tolist()

    labels = []
    for category in df['category'].tolist():
        if category == "positive":
            labels.append(1)
        elif category == "neutral":
            labels.append(0)
        else:
            labels.append(2)  # Negative sentiment

    return texts, labels

# Split the dataset into train and validation sets
texts, labels = load_twitter_data(data_file, num_samples=3000)
train_texts, val_texts, train_labels, val_labels = train_test_split(texts, labels, test_size=0.2, random_state=42)

# Define BERT-specific parameters
bert_model_name = 'bert-base-uncased'
max_length = 128
batch_size = 4
num_epochs = 1
learning_rate = 2e-5

# Load the BERT tokenizer
tokenizer = BertTokenizer.from_pretrained(bert_model_name)

# Define the Twitter classification dataset
class TwitterClassificationDataset(Dataset):
    def __init__(self, texts, labels, tokenizer, max_length):
        self.texts = texts
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        text = self.texts[idx]
        label = self.labels[idx]
        encoding = self.tokenizer(text, return_tensors='pt', max_length=self.max_length, padding='max_length', truncation=True)
        return {'input_ids': encoding['input_ids'].flatten(), 'attention_mask': encoding['attention_mask'].flatten(), 'label': torch.tensor(label)}

# Create dataloaders for training and validation
train_dataset = TwitterClassificationDataset(train_texts, train_labels, tokenizer, max_length)
val_dataset = TwitterClassificationDataset(val_texts, val_labels, tokenizer, max_length)

train_dataloader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_dataloader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)

# Define the BERT-based sentiment classifier
class BERTTwitterClassifier(nn.Module):
    def __init__(self, bert_model_name, num_classes):
        super(BERTTwitterClassifier, self).__init__()
        self.bert = BertForSequenceClassification.from_pretrained(bert_model_name, num_labels=num_classes)

    def forward(self, input_ids, attention_mask):
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        logits = outputs.logits
        return logits

# Create the model and move it to the GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = BERTTwitterClassifier(bert_model_name, num_classes=3).to(device)

# Define the optimizer and learning rate scheduler
optimizer = AdamW(model.parameters(), lr=learning_rate)
total_steps = len(train_dataloader) * num_epochs
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=0, num_training_steps=total_steps)

# Training loop
for epoch in range(num_epochs):
    model.train()
    for batch in train_dataloader:
        optimizer.zero_grad()
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['label'].to(device)
        logits = model(input_ids=input_ids, attention_mask=attention_mask)
        loss = nn.CrossEntropyLoss()(logits, labels)  # Cross-Entropy loss
        loss.backward()
        optimizer.step()
        scheduler.step()

    model.eval()
    val_predictions = []
    val_actual_labels = []

    with torch.no_grad():
        for batch in val_dataloader:
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['label'].to(device)

            logits = model(input_ids=input_ids, attention_mask=attention_mask)
            _, preds = torch.max(logits, dim=1)
            val_predictions.extend(preds.cpu().tolist())
            val_actual_labels.extend(labels.cpu().tolist())

    val_accuracy = accuracy_score(val_actual_labels, val_predictions)
    val_report = classification_report(val_actual_labels, val_predictions, labels=[0, 1, 2], target_names=['neutral', 'positive', 'negative'])

    print(f"Epoch {epoch + 1}/{num_epochs}")
    print(f"Validation Accuracy: {val_accuracy}")
    print(f"Classification Report:\n{val_report}")

# Save the trained model if needed
torch.save(model.state_dict(), 'twitter_sentiment_model.pth')

# Function to predict sentiment for a given text
def predict_sentiment(text, model, tokenizer, device, max_length=128):
    inputs = tokenizer(
        text,
        truncation=True,
        padding=True,
        max_length=max_length,
        return_tensors="pt"
    )
    input_ids = inputs["input_ids"].to(device)
    attention_mask = inputs["attention_mask"].to(device)

    with torch.no_grad():
        logits = model(input_ids=input_ids, attention_mask=attention_mask)
        predicted_class = torch.argmax(logits, dim=1).item()

    if predicted_class == 1:
        return "positive"
    elif predicted_class == 0:
        return "neutral"
    else:
        return "negative"

# Example usage of predict_sentiment
'''text_to_predict = "I love this product!"
predicted_sentiment = predict_sentiment(text_to_predict, model, tokenizer, device)
print(f"Predicted Sentiment: {predicted_sentiment}")'''


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: Undef

Epoch 1/1
Validation Accuracy: 1.0
Classification Report:
              precision    recall  f1-score   support

     neutral       0.00      0.00      0.00         0
    positive       0.00      0.00      0.00         0
    negative       1.00      1.00      1.00       600

   micro avg       1.00      1.00      1.00       600
   macro avg       0.33      0.33      0.33       600
weighted avg       1.00      1.00      1.00       600



'text_to_predict = "I love this product!"\npredicted_sentiment = predict_sentiment(text_to_predict, model, tokenizer, device)\nprint(f"Predicted Sentiment: {predicted_sentiment}")'

In [ ]:
torch.save(model.state_dict(), 'twitter_sentiment_model.pth')


In [ ]:
# Example usage of predict_sentiment
text_to_predict = "I love this product!"
predicted_sentiment = predict_sentiment(text_to_predict, model, tokenizer, device)
print(f"Predicted Sentiment: {predicted_sentiment}")

Predicted Sentiment: negative


In [ ]:
import torch
import torch.nn as nn
from transformers import BertTokenizer, AdamW, get_linear_schedule_with_warmup
from torch.utils.data import DataLoader
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import train_test_split
import pandas as pd

# Load the Twitter dataset
data_file = "/content/drive/MyDrive/Colab Notebooks/Twitter_Data.csv"
df = pd.read_csv(data_file)

# Define a function to load and preprocess the Twitter data
def load_twitter_data(data_file, num_samples=None):
    df = pd.read_csv(data_file)
    if num_samples is not None:
        df = df.sample(num_samples)  # Sample a subset of the data if needed

    texts = df['clean_text'].tolist()

    labels = []
    for category in df['category'].tolist():
        if category == "positive":
            labels.append(1)
        elif category == "neutral":
            labels.append(0)
        else:
            labels.append(2)  # Negative sentiment

    return texts, labels

# Split the dataset into train and validation sets
texts, labels = load_twitter_data(data_file, num_samples=3000)
train_texts, val_texts, train_labels, val_labels = train_test_split(texts, labels, test_size=0.2, random_state=42)

# Define BERT-specific parameters
bert_model_name = 'bert-base-uncased'
max_length = 128
batch_size = 4
num_epochs = 2
learning_rate = 2e-5

# Load the BERT tokenizer
tokenizer = BertTokenizer.from_pretrained(bert_model_name)

# Define the Twitter classification dataset
class TwitterClassificationDataset(Dataset):
    def __init__(self, texts, labels, tokenizer, max_length):
        self.texts = texts
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        text = self.texts[idx]
        label = self.labels[idx]
        encoding = self.tokenizer(text, return_tensors='pt', max_length=self.max_length, padding='max_length', truncation=True)
        return {'input_ids': encoding['input_ids'].flatten(), 'attention_mask': encoding['attention_mask'].flatten(), 'label': torch.tensor(label)}

# Create dataloaders for training and validation
train_dataset = TwitterClassificationDataset(train_texts, train_labels, tokenizer, max_length)
val_dataset = TwitterClassificationDataset(val_texts, val_labels, tokenizer, max_length)

train_dataloader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_dataloader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)

# Define the BERT-based sentiment classifier
class BERTTwitterClassifier(nn.Module):
    def __init__(self, bert_model_name, num_classes):
        super(BERTTwitterClassifier, self).__init__()
        self.bert = BertForSequenceClassification.from_pretrained(bert_model_name, num_labels=num_classes)

    def forward(self, input_ids, attention_mask):
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        logits = outputs.logits
        return logits

# Create the model and move it to the GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Modify the model to output 3 classes (positive, neutral, negative)
model = BERTTwitterClassifier(bert_model_name, num_classes=3).to(device)

# Define the optimizer and learning rate scheduler
optimizer = AdamW(model.parameters(), lr=learning_rate)
total_steps = len(train_dataloader) * num_epochs
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=0, num_training_steps=total_steps)

# Training loop
for epoch in range(num_epochs):
    model.train()
    for batch in train_dataloader:
        optimizer.zero_grad()
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['label'].to(device)
        logits = model(input_ids=input_ids, attention_mask=attention_mask)

        # Use CrossEntropyLoss for multi-class classification
        loss = nn.CrossEntropyLoss()(logits, labels)
        loss.backward()
        optimizer.step()
        scheduler.step()

    model.eval()
    val_predictions = []
    val_actual_labels = []

    with torch.no_grad():
        for batch in val_dataloader:
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['label'].to(device)

            logits = model(input_ids=input_ids, attention_mask=attention_mask)
            _, preds = torch.max(logits, dim=1)
            val_predictions.extend(preds.cpu().tolist())
            val_actual_labels.extend(labels.cpu().tolist())

    val_accuracy = accuracy_score(val_actual_labels, val_predictions)
    val_report = classification_report(val_actual_labels, val_predictions, labels=[0, 1, 2], target_names=['neutral', 'positive', 'negative'])

    print(f"Epoch {epoch + 1}/{num_epochs}")
    print(f"Validation Accuracy: {val_accuracy}")
    print(f"Classification Report:\n{val_report}")


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: Undef

Epoch 1/2
Validation Accuracy: 1.0
Classification Report:
              precision    recall  f1-score   support

     neutral       0.00      0.00      0.00         0
    positive       0.00      0.00      0.00         0
    negative       1.00      1.00      1.00       600

   micro avg       1.00      1.00      1.00       600
   macro avg       0.33      0.33      0.33       600
weighted avg       1.00      1.00      1.00       600

Epoch 2/2
Validation Accuracy: 1.0
Classification Report:
              precision    recall  f1-score   support

     neutral       0.00      0.00      0.00         0
    positive       0.00      0.00      0.00         0
    negative       1.00      1.00      1.00       600

   micro avg       1.00      1.00      1.00       600
   macro avg       0.33      0.33      0.33       600
weighted avg       1.00      1.00      1.00       600



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.

In [ ]:
class TwitterClassificationDataset(Dataset):
    def __init__(self, texts, labels, tokenizer, max_length):
        self.texts = texts
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.texts)

    def __getitem__(self, idx):
        text = self.texts[idx]
        label = self.labels[idx]

        # Tokenize the single text input
        encoding = self.tokenizer(
            text,
            return_tensors='pt',
            max_length=self.max_length,
            padding='max_length',
            truncation=True
        )

        return {'input_ids': encoding['input_ids'].flatten(), 'attention_mask': encoding['attention_mask'].flatten(), 'label': torch.tensor(label)}


In [ ]:
# Example usage of predict_sentiment
text_to_predict = "The weather is cold."
predicted_sentiment = predict_sentiment(text_to_predict, model, tokenizer, device)
print(f"Predicted Sentiment: {predicted_sentiment}")

Predicted Sentiment: negative


In [ ]:
!pip install nbconvert


In [ ]:
from nbconvert import HTMLExporter
import nbformat

# Load the notebook
notebook_path = '/content/drive/MyDrive/Colab Notebooks/sentiment_analysis_Twitter.ipynb'
with open(notebook_path) as f:
    notebook_content = nbformat.read(f, as_version=4)

# Convert the notebook to HTML using the default template
html_exporter = HTMLExporter()
(body, resources) = html_exporter.from_notebook_node(notebook_content)

# Save the HTML content to a file
html_output_path = 'notebook.html'
with open(html_output_path, 'w', encoding='utf-8') as f:
    f.write(body)


In [ ]:
!jupyter nbconvert --to html sentiment_analysis_Twitter.ipynb

[NbConvertApp] WARNING | pattern 'sentiment_analysis_Twitter.ipynb' matched no files
This application is used to convert notebook files (*.ipynb)
        to various other formats.


Options
The options below are convenience aliases to configurable class-options,
as listed in the "Equivalent to" description-line of the aliases.
To see all configurable class-options for some <cmd>, use:
    <cmd> --help-all

--debug
    set log level to logging.DEBUG (maximize logging output)
    Equivalent to: [--Application.log_level=10]
--show-config
    Show the application's configuration (human-readable format)
    Equivalent to: [--Application.show_config=True]
--show-config-json
    Show the application's configuration (json format)
    Equivalent to: [--Application.show_config_json=True]
--generate-config
    generate default config file
    Equivalent to: [--JupyterApp.generate_config=True]
-y
    Answer yes to any questions instead of prompting.
    Equivalent to: [--JupyterApp.answer_yes=True